In [398]:
import pandas as pd
import numpy as np

# read in the data
data = pd.read_csv(r"C:\Users\Phoebe Tan\OneDrive - National University of Singapore\Desktop\Taiwan\Data Mining\train.csv", sep=',', header=0, skipinitialspace=True)
data.columns = [col.strip() for col in data.columns]
data['ItemName']=data['ItemName'].str.strip()

# Load the data from CSV
df=data

# Convert the 'Date' column to a datetime format
df['Date'] = pd.to_datetime(df['Date'])

# Group the data by item name and date
grouped = df.groupby(['ItemName', 'Date'])

# Create an empty list to store the new rows of data
new_rows = []

# Loop through each group
for name, group in grouped:
    # Get the values for the current group
    values = group.iloc[:, 3:].values.flatten()

    # Split the values into chunks of 10 hours
    chunks = [values[i:i+10] for i in range(0, len(values), 10)]
    # Add the rows to the new_rows list
    for chunk in chunks:
        new_row = {'ItemName': name[0]}
        new_row.update(dict(zip(['Hour '+str(i+1) for i in range(10)], chunk)))
        new_rows.append(new_row)
# If there aren't enough hours to fill a row, store the leftover hours


# Create a new DataFrame from the new_rows list
new_df = pd.DataFrame(new_rows)
new_cols=new_df.columns
# Create a new DataFrame to store the reformatted data
reformatted_df = pd.DataFrame(columns=new_cols)



# iterate over each unique item in the original dataframe
for item in new_df['ItemName'].unique():
    # get the rows for the current item
    item_rows = new_df[new_df['ItemName'] == item]
    # create a new row for the current item in the new dataframe
    new_row = {col: np.nan for col in new_cols}
    new_row['ItemName'] = item
    # fill in values for the current item in the new row
    colno=1
    # Iterate over the rows of item_rows
    for i, row in item_rows.iterrows(): 
        col_name = f'Hour {colno}'   
        for col in item_rows.columns[1:]:
            col_name = f'Hour {colno}'   
            if not pd.isna(row[col]):
                new_row[col_name]=row[col]
                colno+=1
                if colno==11:
                    reformatted_df = reformatted_df.append(new_row, ignore_index=True)
                    new_row = {col: np.nan for col in new_cols}
                    new_row['ItemName'] = item       
                    colno=1
                else:
                    continue            
            else:
                continue
                
            
# Save the new DataFrame to CSV
#reformatted_df.to_csv('reformatted_data5.csv', index=False)    
df=reformatted_df
df.insert(0, 'id', 0)

# Define a function to label rows with a unique id for each itemset
def label_rows_with_id(group):
    group['id'] = range(len(group))
    return group

# Group the DataFrame by 'ItemName' and apply the label_rows_with_id function to each group
df = df.groupby('ItemName').apply(label_rows_with_id)

# Reset the index of the DataFrame
df = df.reset_index(drop=True)

print(df['ItemName'].unique())

['AMB_TEMP' 'CH4' 'CO' 'NMHC' 'NO' 'NO2' 'NOx' 'O3' 'PM10' 'PM2.5'
 'RAINFALL' 'RH' 'SO2' 'THC' 'WD_HR' 'WIND_DIREC' 'WIND_SPEED' 'WS_HR']


In [399]:
# replace the invalid values with NaN
df = df.replace(['AMB_TEMP'], 'TEMP', regex=True)
df = df.replace(['RAINFALL'], 'RF', regex=True)
df = df.replace(['NOx'], 'NO3', regex=True)
df = df.replace(['#\s*', '\*\s*', 'x\s*', 'A\s*'], pd.NA, regex=True)
df = df.replace(['TEMP'], 'AMB_TEMP', regex=True)
df = df.replace(['NO3'], 'NOX', regex=True)
df = df.replace(['RF'], 'RAINFALL', regex=True)

df[['Hour 1', 'Hour 2', 'Hour 3', 'Hour 4', 'Hour 5','Hour 6', 'Hour 7', 'Hour 8', 'Hour 9', 'Hour 10']]= df[['Hour 1', 'Hour 2', 'Hour 3', 'Hour 4', 'Hour 5',
'Hour 6', 'Hour 7', 'Hour 8', 'Hour 9', 'Hour 10']].apply(pd.to_numeric)

# Find the row indices with at least one NaN value
nan_rows = df.isna().any(axis=1)

# Print the number of rows with NA values
print('Number of rows with NA values:',sum(nan_rows==True))

nullrows= df[ df.isna().any(axis=1)==True]
print(nullrows)
print('Number of rows with NA values',len(nullrows['id'].unique()))


# print the number of unique ItemNames
num_unique_ids = len(df['ItemName'].unique())
print('Number of rows unique ItemNames:',num_unique_ids)


print(df.columns)

#df.to_csv("df2.csv", index=False)

Number of rows with NA values: 631
       id    ItemName  Hour 1  Hour 2  Hour 3  Hour 4  Hour 5  Hour 6  Hour 7  \
60     60    AMB_TEMP   17.40     NaN    16.9   16.70   16.20   16.00   15.80   
66     66    AMB_TEMP     NaN     NaN    22.8   22.30   21.20   19.80   19.10   
86     86    AMB_TEMP   18.50   18.40    18.2   18.10   18.20   18.00     NaN   
565   565    AMB_TEMP   23.10     NaN    22.1   22.60   24.40   23.90   23.10   
589    13         CH4    1.97    1.98     NaN    1.97    1.97    1.98    1.98   
...   ...         ...     ...     ...     ...     ...     ...     ...     ...   
9661  445  WIND_SPEED    1.70    1.60     NaN    2.50    3.40    3.30    1.30   
9848   56       WS_HR    0.60    0.40     0.5    1.30    1.40    1.50    0.50   
9852   60       WS_HR    0.50     NaN     0.5    0.70    0.90    0.70    0.50   
9858   66       WS_HR     NaN     NaN     4.0    3.90    4.30    4.00    3.90   
9878   86       WS_HR    0.60    0.90     1.3    1.80    2.00    2.10     

In [400]:
# get the number of rows
num_rows = df.shape[0]

# print the number of rows
print('Number of rows:',num_rows)


print(df)

df=df.interpolate()
#df.to_csv("df3.csv", index=False)


Number of rows: 10368
        id  ItemName  Hour 1  Hour 2  Hour 3  Hour 4  Hour 5  Hour 6  Hour 7  \
0        0  AMB_TEMP    11.1    11.2    11.4    11.5    11.6    11.7    11.9   
1        1  AMB_TEMP    14.9    15.7    16.1    16.6    16.6    16.3    15.6   
2        2  AMB_TEMP    14.7    14.7    14.6    14.4    14.4    14.2    14.2   
3        3  AMB_TEMP    13.8    13.7    14.1    15.1    16.6    17.4    18.5   
4        4  AMB_TEMP    16.7    15.8    15.6    15.6    15.6    15.7    15.6   
...    ...       ...     ...     ...     ...     ...     ...     ...     ...   
10363  571     WS_HR     3.2     3.5     3.1     3.2     3.6     3.1     3.0   
10364  572     WS_HR     3.1     3.7     3.7     3.4     3.5     3.1     2.7   
10365  573     WS_HR     2.7     1.9     1.8     1.5     1.1     0.6     0.5   
10366  574     WS_HR     0.8     0.3     0.5     0.4     0.9     0.7     0.2   
10367  575     WS_HR     0.6     0.4     1.0     0.5     0.5     0.3     0.1   

       Hour 8  Ho

In [401]:
# calculate the mean and median of the Hour 1 to 9 columns
df["Mean"] = df.iloc[:, 2:11].mean(axis=1)
df["Median"] = df.iloc[:, 2:11].median(axis=1)

# calculate the means for each subset of columns
df["Mean1"] = df.iloc[:, 2:4].mean(axis=1)
df["Mean2"] = df.iloc[:, 5:7].mean(axis=1)
df["Mean3"] = df.iloc[:, 8:10].mean(axis=1)

#df.to_csv("df4.csv", index=False)
num_unique_ids = len(df['ItemName'].unique())
print(df['ItemName'].unique())

['AMB_TEMP' 'CH4' 'CO' 'NMHC' 'NO' 'NO2' 'NOX' 'O3' 'PM10' 'PM2.5'
 'RAINFALL' 'RH' 'SO2' 'THC' 'WD_HR' 'WIND_DIREC' 'WIND_SPEED' 'WS_HR']


In [402]:
# Find the row indices with at least one NaN value
nan_rows =df.isna().any(axis=1)

# Print the number of rows with NA values
print(nan_rows[nan_rows==True])

# Save new data to a new CSV file
#df.to_csv("df6.csv", index=False)

Series([], dtype: bool)


In [403]:
# Feature selection: Aggregation (Method 1- Take 1) Take mean of the 9hours data as a feature for each variable to predict 10 hours)

# Create a list of column names
columns = ['AMB_TEMP', 'CH4', 'CO', 'NMHC', 'NO', 'NO2', 'NOX', 'O3', 'PM10', 'PM2.5','RAINFALL', 'RH', 'SO2', 'THC', 'WD_HR', 'WIND_DIREC', 'WIND_SPEED','WS_HR','Output']
# Create an empty DataFrame with the specified columns
method1 = pd.DataFrame(columns=columns)
method1['Output']=pd.to_numeric(method1["Output"])

# insert Id column at beginning
method1.insert(0, 'id', range(0, 576))


# iterate through each id
for i in range(576):
    id_df = df.loc[df['id'] == i] # select rows with the iterated id value
    for index, row in id_df.iterrows():
        item_name = row['ItemName']
        mean =row['Mean']
        method1.loc[method1['id'] == i,item_name] = mean # add the value in the Mean column to the new dataset column='ItemName' where 'ItemName'= item name of the value in 'ItemName' column of the iterated row
        # add PM2.5 value in Hour 10 of the iterated index to the new dataset column 'Output'
        if item_name=="PM2.5":
            pm25_value=row['Hour 10']
            method1.loc[method1['id'] == i, 'Output'] = pm25_value
        else:
            continue
   
        
# print the new dataset
print(method1)

data=method1

      id   AMB_TEMP       CH4        CO      NMHC        NO        NO2  \
0      0  11.688889  2.014444  0.291111  0.087778  1.666667  10.666667   
1      1  15.666667  1.993333  0.318889  0.086667  3.244444  10.677778   
2      2  14.433333       2.0  0.282222  0.071111  1.166667   9.344444   
3      3  16.188889  1.971111  0.331111  0.068889  2.044444   8.422222   
4      4       15.6  2.013333  0.366667  0.073333       1.2       11.1   
..   ...        ...       ...       ...       ...       ...        ...   
571  571  15.788889  1.993333      0.18  0.033333  0.755556   5.477778   
572  572  19.511111  1.978889  0.228889      0.05  1.777778   7.122222   
573  573  16.933333  2.063333  0.284444  0.076667  1.011111  15.777778   
574  574  18.077778  2.116667  0.397778  0.146667  5.977778  23.566667   
575  575  19.088889  2.252222  0.791111  0.287778  9.355556  33.977778   

           NOX         O3       PM10      PM2.5  RAINFALL         RH  \
0         12.4  23.988889       28.0  1

In [404]:
# Find the row indices with at least one NaN value
nan_rows =method1.isna().any(axis=1)

# Print the number of rows with NA values
print(nan_rows[nan_rows==True])

# Save new data to a new CSV file
#method1.to_csv("df7.csv", index=False)

Series([], dtype: bool)


In [405]:


# Find the row indices with at least one NaN value
nan_rows =df.isna().any(axis=1)

# Print the number of rows with NA values
print('Number of rows with NA values:',sum(nan_rows==True))

# get the number of rows
num_rows = df.shape[0]

# print the number of rows
print('Number of rows before dropping NA values:',num_rows)


# print the number of unique IDs
num_unique_ids = len(df['id'].unique())
print('Number of Unique IDs before dropping NA values:',num_unique_ids)

# print the number of unique ItemNames before dropping NA values
num_unique_ids = len(df['ItemName'].unique())
print('Number of Unique ItemNames before dropping NA values:',num_unique_ids)
print(df['ItemName'].unique())



#Drop NA Values
df = df.dropna()

# Find the row indices with at least one NaN value
nan_rows =df.isna().any(axis=1)

# Print the number of rows with NA values
print('Number of rows with NA values after dropping NA values:',sum(nan_rows==True))

# get the number of rows
num_rows = df.shape[0]

# print the number of rows
print('Number of rows after dropping NA values:',num_rows)

# print the number of unique IDs
num_unique_ids = len(df['id'].unique())
print('Number of Unique IDs after dropping NA values:',num_unique_ids)

# print the number of unique ItemNames after dropping NA values
num_unique_ids = len(df['ItemName'].unique())
print('Number of Unique ItemNames after dropping NA values:',num_unique_ids)
print(df['ItemName'].unique())

# print dataframe
print(df)




#cannot simply drop NA values since it will result in one less ItemName.


# loop through each row and estimate missing values
#for i, row in df.iterrows():
#    row_mean = row['Hour 1':'Hour 10'].mean()  # calculate row mean
#    df.loc[i, 'Hour 1':'Hour 10'] = row['Hour 1':'Hour 10'].fillna(row_mean)

    
# Find the row indices with at least one NaN value
#nan_rows =df.isna().any(axis=1)
#nan_rows[(nan_rows==True)]
# Print the number of rows with NA values
#print(sum(nan_rows==True))


Number of rows with NA values: 0
Number of rows before dropping NA values: 10368
Number of Unique IDs before dropping NA values: 576
Number of Unique ItemNames before dropping NA values: 18
['AMB_TEMP' 'CH4' 'CO' 'NMHC' 'NO' 'NO2' 'NOX' 'O3' 'PM10' 'PM2.5'
 'RAINFALL' 'RH' 'SO2' 'THC' 'WD_HR' 'WIND_DIREC' 'WIND_SPEED' 'WS_HR']
Number of rows with NA values after dropping NA values: 0
Number of rows after dropping NA values: 10368
Number of Unique IDs after dropping NA values: 576
Number of Unique ItemNames after dropping NA values: 18
['AMB_TEMP' 'CH4' 'CO' 'NMHC' 'NO' 'NO2' 'NOX' 'O3' 'PM10' 'PM2.5'
 'RAINFALL' 'RH' 'SO2' 'THC' 'WD_HR' 'WIND_DIREC' 'WIND_SPEED' 'WS_HR']
        id  ItemName  Hour 1  Hour 2  Hour 3  Hour 4  Hour 5  Hour 6  Hour 7  \
0        0  AMB_TEMP    11.1    11.2    11.4    11.5    11.6    11.7    11.9   
1        1  AMB_TEMP    14.9    15.7    16.1    16.6    16.6    16.3    15.6   
2        2  AMB_TEMP    14.7    14.7    14.6    14.4    14.4    14.2    14.2   


In [406]:
df[['Hour 1', 'Hour 2', 'Hour 3', 'Hour 4', 'Hour 5','Hour 6', 'Hour 7', 'Hour 8', 'Hour 9', 'Hour 10']]= df[['Hour 1', 'Hour 2', 'Hour 3', 'Hour 4', 'Hour 5',
'Hour 6', 'Hour 7', 'Hour 8', 'Hour 9', 'Hour 10']].apply(pd.to_numeric)

# calculate the mean and median of the Hour 1 to 9 columns
df["Mean"] = df.iloc[:, 2:11].mean(axis=1)
df["Median"] = df.iloc[:, 2:11].median(axis=1)

# calculate the means for each subset of columns
df["Mean1"] = df.iloc[:, 2:4].mean(axis=1)
df["Mean2"] = df.iloc[:, 5:7].mean(axis=1)
df["Mean3"] = df.iloc[:, 8:10].mean(axis=1)

# print out the updated DataFrame
print(df)


# Find the row indices with at least one NaN value
nan_rows =df.isna().any(axis=1)

# Print the number of rows with NA values
print(sum(nan_rows==True))

# Save new data to a new CSV file
df.to_csv("df.csv", index=False)

        id  ItemName  Hour 1  Hour 2  Hour 3  Hour 4  Hour 5  Hour 6  Hour 7  \
0        0  AMB_TEMP    11.1    11.2    11.4    11.5    11.6    11.7    11.9   
1        1  AMB_TEMP    14.9    15.7    16.1    16.6    16.6    16.3    15.6   
2        2  AMB_TEMP    14.7    14.7    14.6    14.4    14.4    14.2    14.2   
3        3  AMB_TEMP    13.8    13.7    14.1    15.1    16.6    17.4    18.5   
4        4  AMB_TEMP    16.7    15.8    15.6    15.6    15.6    15.7    15.6   
...    ...       ...     ...     ...     ...     ...     ...     ...     ...   
10363  571     WS_HR     3.2     3.5     3.1     3.2     3.6     3.1     3.0   
10364  572     WS_HR     3.1     3.7     3.7     3.4     3.5     3.1     2.7   
10365  573     WS_HR     2.7     1.9     1.8     1.5     1.1     0.6     0.5   
10366  574     WS_HR     0.8     0.3     0.5     0.4     0.9     0.7     0.2   
10367  575     WS_HR     0.6     0.4     1.0     0.5     0.5     0.3     0.1   

       Hour 8  Hour 9  Hour 10       Me

In [407]:
for i in range(576):
    id_df= df.loc[df['id']==i]
    for index, row in id_df.iterrows():
        print (row)
        print(row['Mean'])

id                  0
ItemName     AMB_TEMP
Hour 1           11.1
Hour 2           11.2
Hour 3           11.4
Hour 4           11.5
Hour 5           11.6
Hour 6           11.7
Hour 7           11.9
Hour 8           12.1
Hour 9           12.7
Hour 10          13.9
Mean        11.688889
Median           11.6
Mean1           11.15
Mean2           11.55
Mean3            12.0
Name: 0, dtype: object
11.68888888888889
id                 0
ItemName         CH4
Hour 1          2.01
Hour 2          1.99
Hour 3           2.0
Hour 4          2.02
Hour 5          2.03
Hour 6          2.02
Hour 7          2.02
Hour 8          2.01
Hour 9          2.03
Hour 10         2.03
Mean        2.014444
Median          2.02
Mean1            2.0
Mean2          2.025
Mean3          2.015
Name: 576, dtype: object
2.0144444444444445
id                 0
ItemName          CO
Hour 1          0.31
Hour 2          0.28
Hour 3          0.28
Hour 4          0.33
Hour 5          0.32
Hour 6          0.26
Hour 7          

In [408]:
# Feature selection: Aggregation (Method 1- Take 1) Take mean of the 9hours data as a feature for each variable to predict 10 hours)

# Create a list of column names
columns = ['AMB_TEMP', 'CH4', 'CO', 'NMHC', 'NO', 'NO2', 'O3', 'PM10', 'PM2.5', 'RH', 'SO2', 'THC','WD_HR', 'WIND_DIREC', 'WIND_SPEED', 'WS_HR', 'Output']

# Create an empty DataFrame with the specified columns
method1 = pd.DataFrame(columns=columns)


# insert Id column at beginning
method1.insert(0, 'id', range(0, 575))


# iterate through each id
for i in range(575):
    id_df = df.loc[df['id'] == i] # select rows with the iterated id value
    for index, row in id_df.iterrows():
        item_name = row['ItemName']
        mean =row['Mean']
        method1.loc[method1['id'] == i,item_name] = mean # add the value in the Mean column to the new dataset column='ItemName' where 'ItemName'= item name of the value in 'ItemName' column of the iterated row
        # add PM2.5 value in Hour 10 of the iterated index to the new dataset column 'Output'
        if item_name=="PM2.5":
            pm25_value=row['Hour 10']
            method1.loc[method1['id'] == i, 'Output'] = pm25_value
        else:
            continue
   
        
# print the new dataset
print(method1)


# Save new data to a new CSV file
#method1.to_csv("method1.csv", index=False)

data=method1




      id   AMB_TEMP       CH4        CO      NMHC        NO        NO2  \
0      0  11.688889  2.014444  0.291111  0.087778  1.666667  10.666667   
1      1  15.666667  1.993333  0.318889  0.086667  3.244444  10.677778   
2      2  14.433333       2.0  0.282222  0.071111  1.166667   9.344444   
3      3  16.188889  1.971111  0.331111  0.068889  2.044444   8.422222   
4      4       15.6  2.013333  0.366667  0.073333       1.2       11.1   
..   ...        ...       ...       ...       ...       ...        ...   
570  570  16.066667  2.001111  0.261111  0.083333  1.277778  10.677778   
571  571  15.788889  1.993333      0.18  0.033333  0.755556   5.477778   
572  572  19.511111  1.978889  0.228889      0.05  1.777778   7.122222   
573  573  16.933333  2.063333  0.284444  0.076667  1.011111  15.777778   
574  574  18.077778  2.116667  0.397778  0.146667  5.977778  23.566667   

            O3       PM10      PM2.5         RH       SO2       THC  \
0    23.988889       28.0  14.888889  63

In [409]:
import matplotlib.pyplot as plt

# drop the 'id' column
#data = data.drop('id', axis=1)
X = data.drop('Output', axis=1)
X = np.array(X)


### Step 1: Standardize the Data along the Features
standardized_data = (X - np.mean(X, axis=0)) / np.std(X)

### Step 2: Calculate the Covariance Matrix
covariance_matrix = np.cov(standardized_data.astype(float), ddof = 0, rowvar = False)


### Step 3: Eigendecomposition on the Covariance Matrix
eigenvalues, eigenvectors = np.linalg.eig(covariance_matrix)


### Step 4: Sort the Principal Components
# np.argsort can only provide lowest to highest; use [::-1] to reverse the list
order_of_importance = np.argsort(eigenvalues)[::-1] 

# utilize the sort order to sort eigenvalues and eigenvectors
sorted_eigenvalues = eigenvalues[order_of_importance]
sorted_eigenvectors = eigenvectors[:,order_of_importance] # sort the columns


### Step 5: Calculate the Explained Variance
# use sorted_eigenvalues to ensure the explained variances correspond to the eigenvectors
explained_variance = sorted_eigenvalues / np.sum(sorted_eigenvalues)


### Step 6: Reduce the Data via the Principal Components
k = 3 # select the number of principal components
reduced_data = np.matmul(standardized_data, sorted_eigenvectors[:,:k]) # transform the original data



In [410]:
print(reduced_data)

[[-3.346273615334055 -1.570099979638407 -0.1343595911778862]
 [-3.3349064101689936 -1.670357956058241 -0.03511139016755781]
 [-3.322696087986742 -1.5324411099288415 -0.13808385613110213]
 ...
 [3.341184279392219 -1.3767957092505916 0.10648253362178232]
 [3.352928027819292 -1.3992929556179456 -0.05028067982025821]
 [3.354207592468768 -0.27285186908795345 0.01056454001087564]]


In [411]:
#Performing Linear Regression on PCA features (k=3)
y  = data['Output']
y = np.array(y)
X= reduced_data

pred = np.zeros(X.shape[0])
# Normalize the features to have zero mean and unit variance
X = (X - np.mean(X, axis=0)) / np.std(X.astype(float), axis=0)
# Define initial bias, weight, learning rate, iteration, and regularization parameter
b = 0.0
w = np.zeros(X.shape[1])
lr = 0.01
iteration = 1000000
reg_param = 0.1

# Initialize Adagrad learning rate parameters
lr_b = 0.0
lr_w = np.zeros(X.shape[1])

# Perform stochastic gradient descent with Adagrad
for i in range(iteration):
    # Randomly select a single sample
    j = np.random.randint(X.shape[0])
    
    y_pred = np.dot(w, X[j]) + b
    b_grad = -2.0*(y[j] - y_pred) * 1
    w_grad = -2.0*(y[j] - y_pred) * X[j]
        
    # Add regularization to the weight gradient
    w_grad += 2*reg_param * w
    
    # Update Adagrad learning rate parameters
    lr_b += b_grad ** 2
    lr_w = lr_w+ w_grad ** 2
    
    # Update bias and weight using Adagrad learning rate
    b -= lr / np.sqrt(lr_b) * b_grad
    w = w- lr / ((lr_w)**0.5) * w_grad

# Print the final bias and weight values
print('Final bias:', b)
print('Final weights:', w)

# Calculate the predicted values using the final bias and weights
pred = np.dot(X, w) + b
print(pred)



Final bias: 11.214936390653975
Final weights: [-1.5240517440259642 -0.17051169851547768 3.4798846347355203]
[11.770378723575583 13.44913525306729 11.684287728378116
 11.439110184662756 8.818517319547762 8.965962569994714 12.495715720434923
 8.963470490885554 8.769199898019195 7.345727756952009 8.414033800680128
 9.211192600057139 8.509196593425917 10.40630706249959 7.8154148740987495
 8.335659397313242 8.608784630873682 9.202495064024202 11.84582505102449
 11.65093206494356 13.638672522726477 12.658398707453475
 11.601249826810708 11.079964234894959 9.212637048926506
 11.618786086317215 11.653721270001656 18.654856945672897 18.8575369143135
 12.684705947738628 19.13931952024375 10.968339773888426
 16.275724167975582 16.382871433067315 13.68177692381225 18.82676501012385
 12.276374802198267 22.505028728181976 16.524206453986036
 14.470097639166378 15.409557724027927 16.2503473164368 15.77050036385581
 10.555090977136341 12.417695728479934 9.547937869405128
 12.062084302764998 16.6747506

In [412]:
#RMSE: Above uses all training data to train the model
deviation=0
for j in range(X.shape[0]):
        y_pred = np.dot(w, X[j]) + b        
        deviation+= (y[j]-y_pred)**2
print(X.shape[0])
print(deviation)
RMSE= np.sqrt(deviation/X.shape[0])
print(RMSE)

575
35246.401254633856
7.829309620809083


In [413]:
#Using 100% of dataset as Training set


# print the updated DataFrame
print(data.head())
# Separate features (X) and labels (y) from data

X = data.drop('Output', axis=1)
X = np.array(X)

y  = data['Output']
y = np.array(y)
print(y)

# Normalize the features to have zero mean and unit variance
X = (X - np.mean(X, axis=0)) / np.std(X)

pred = np.zeros(X.shape[0])
# Define initial bias, weight, learning rate, iteration, and regularization parameter
b = 0.0
w = np.zeros(X.shape[1])
lr = 0.01
iteration = 10000
reg_param = 0.1

# Initialize Adagrad learning rate parameters
lr_b = 0.0
lr_w = np.zeros(X.shape[1])

# Perform gradient descent with Adagrad
for i in range(iteration):
    b_grad = 0.0
    w_grad = np.zeros(X.shape[1],dtype=float)
    w_grad=w_grad.astype(float)
    for j in range(X.shape[0]):
        y_pred = np.dot(w, X[j]) + b
        b_grad += -2.0*(y[j] - y_pred) * 1
        w_grad = w_grad + -2.0*(y[j] - y_pred) * X[j]
        
    # Add regularization to the weight gradient
    w_grad += 2*reg_param * w
    # Update Adagrad learning rate parameters
    lr_b += b_grad ** 2
    lr_w = lr_w+ w_grad ** 2
    # Update bias and weight using Adagrad learning rate
    b -= lr / np.sqrt(lr_b) * b_grad
    w = w- lr / ((lr_w)**0.5) * w_grad

# Print the final bias and weight values
print('Final bias:', b)
print('Final weights:', w)


for j in range(X.shape[0]):
    y_pred = np.dot(w, X[j]) + b
    pred[j]=y_pred

print(pred)


   id   AMB_TEMP       CH4        CO      NMHC        NO        NO2  \
0   0  11.688889  2.014444  0.291111  0.087778  1.666667  10.666667   
1   1  15.666667  1.993333  0.318889  0.086667  3.244444  10.677778   
2   2  14.433333       2.0  0.282222  0.071111  1.166667   9.344444   
3   3  16.188889  1.971111  0.331111  0.068889  2.044444   8.422222   
4   4       15.6  2.013333  0.366667  0.073333       1.2       11.1   

          O3       PM10      PM2.5         RH       SO2       THC      WD_HR  \
0  23.988889       28.0  14.888889  63.222222  9.588889  2.102222  43.222222   
1  31.777778  33.111111  13.888889  55.666667  1.333333      2.08  40.555556   
2  32.344444  26.888889  11.888889  68.777778  1.522222  2.071111  45.888889   
3  36.044444  22.444444   8.777778  61.222222  3.133333      2.04  46.222222   
4  31.955556  10.333333   6.444444  69.777778  3.377778  2.086667  72.888889   

  WIND_DIREC WIND_SPEED     WS_HR Output        NOX  RAINFALL  
0  44.555556   2.911111  2.3

In [ ]:
#Using 100% of dataset as Training set
# drop the 'id' column
#data = data.drop('id', axis=1)

# print the updated DataFrame
print(data.head())
# Separate features (X) and labels (y) from data

X = data.drop('Output', axis=1)
X = np.array(X)

y  = data['Output']
y = np.array(y)
print(y)

# Normalize the features to have zero mean and unit variance
X = (X - np.mean(X, axis=0)) / np.std(X)
# Define initial bias, weight, learning rate, iteration, and regularization parameter
b = 0.0
w = np.zeros(X.shape[1])
lr = 0.01
iteration = 5000000
reg_param = 0.1

# Initialize Adagrad learning rate parameters
lr_b = 0.0
lr_w = np.zeros(X.shape[1])

# Perform stochastic gradient descent with Adagrad
for i in range(iteration):
    # Randomly select a single sample
    j = np.random.randint(X.shape[0])
    
    y_pred = np.dot(w, X[j]) + b
    b_grad = -2.0*(y[j] - y_pred) * 1
    w_grad = -2.0*(y[j] - y_pred) * X[j]
        
    # Add regularization to the weight gradient
    w_grad += 2*reg_param * w
    
    # Update Adagrad learning rate parameters
    lr_b += b_grad ** 2
    lr_w = lr_w+ w_grad ** 2
    
    # Update bias and weight using Adagrad learning rate
    b -= lr / np.sqrt(lr_b) * b_grad
    w = w- lr / ((lr_w)**0.5) * w_grad

# Print the final bias and weight values
print('Final bias:', b)
print('Final weights:', w)

# Calculate the predicted values using the final bias and weights
pred = np.dot(X, w) + b
print(pred)


   id   AMB_TEMP       CH4        CO      NMHC        NO        NO2  \
0   0  11.688889  2.014444  0.291111  0.087778  1.666667  10.666667   
1   1  15.666667  1.993333  0.318889  0.086667  3.244444  10.677778   
2   2  14.433333       2.0  0.282222  0.071111  1.166667   9.344444   
3   3  16.188889  1.971111  0.331111  0.068889  2.044444   8.422222   
4   4       15.6  2.013333  0.366667  0.073333       1.2       11.1   

          O3       PM10      PM2.5         RH       SO2       THC      WD_HR  \
0  23.988889       28.0  14.888889  63.222222  9.588889  2.102222  43.222222   
1  31.777778  33.111111  13.888889  55.666667  1.333333      2.08  40.555556   
2  32.344444  26.888889  11.888889  68.777778  1.522222  2.071111  45.888889   
3  36.044444  22.444444   8.777778  61.222222  3.133333      2.04  46.222222   
4  31.955556  10.333333   6.444444  69.777778  3.377778  2.086667  72.888889   

  WIND_DIREC WIND_SPEED     WS_HR Output        NOX  RAINFALL  
0  44.555556   2.911111  2.3

In [ ]:
#RMSE: Above uses all training data to train the model
deviation=0
for j in range(X.shape[0]):
        y_pred = np.dot(w, X[j]) + b        
        deviation+= (y[j]-y_pred)**2
print(X.shape[0])
print(deviation)
RMSE= np.sqrt(deviation/X.shape[0])

In [ ]:
RMSE

In [ ]:
#Using a 75% training data set split and 25% validation set split approach
np.random.seed(44)

# Shuffle the DataFrame randomly
data = data.sample(frac=1, random_state=42)

# Calculate the split point
split_point = int(0.75 * len(data))

# Split the DataFrame into training and validation sets
train = data[:split_point]
validation = data[split_point:]


print(len(train))
print(len(validation))




In [ ]:
originaldata=data
data=train
# Separate features (X) and labels (y) from data

X = data.drop('Output', axis=1)
print(X)
X = np.array(X)

y  = data['Output']
y = np.array(y)
print(y)


# Normalize the features to have zero mean and unit variance
X = (X - np.mean(X, axis=0)) / np.std(X)


# Define initial bias, weight, learning rate, iteration, and regularization parameter
b = 0.0
w = np.zeros(X.shape[1])
lr = 0.01
iteration = 1000
reg_param = 0.1

# Initialize Adagrad learning rate parameters
lr_b = 0.0
lr_w = np.zeros(X.shape[1])

# Perform gradient descent with Adagrad
for i in range(iteration):
    b_grad = 0.0
    w_grad = np.zeros(X.shape[1],dtype=float)
    w_grad=w_grad.astype(float)
    for j in range(X.shape[0]):
        y_pred = np.dot(w, X[j]) + b
        b_grad += -2.0*(y[j] - y_pred) * 1
        w_grad = w_grad + -2.0*(y[j] - y_pred) * X[j]
        
    # Add regularization to the weight gradient
    w_grad += 2*reg_param * w
    # Update Adagrad learning rate parameters
    lr_b += b_grad ** 2
    lr_w = lr_w+ w_grad ** 2
    # Update bias and weight using Adagrad learning rate
    b -= lr / np.sqrt(lr_b) * b_grad
    w = w- lr / ((lr_w)**0.5) * w_grad

# Print the final bias and weight values
print('Final bias:', b)
print('Final weights:', w)

In [288]:
#TRAINING RMSE: Above uses 75% data to train the model
deviation=0
for j in range(X.shape[0]):
        y_pred = np.dot(w, X[j]) + b        
        deviation+= (y[j]-y_pred)**2

RMSE= np.sqrt(deviation/X.shape[0])
print(RMSE)

16.09288291753191


In [289]:
#TEST RMSE: Above uses 25% data to validate the model
deviation=0
data=validation

X = data.drop('Output', axis=1)
print(X)
X = np.array(X)

y  = data['Output']
y = np.array(y)
print(y)

# Normalize the features to have zero mean and unit variance
X = (X - np.mean(X, axis=0)) / np.std(X)


for j in range(X.shape[0]):
        y_pred = np.dot(w, X[j]) + b        
        deviation+= (y[j]-y_pred)**2

RMSE= np.sqrt(deviation/X.shape[0])
print(RMSE)

      AMB_TEMP       CH4        CO      NMHC        NO        NO2         O3  \
351  25.755556  2.011111  0.281111  0.084444       1.1   9.711111  29.288889   
479       25.6  2.017778  0.272222  0.115556       0.8  11.355556  39.455556   
178  20.255556  2.111111  0.376667  0.146667  3.733333  18.711111  29.333333   
493  27.211111  2.002222      0.31  0.067778       1.1   8.011111  45.833333   
41        13.6  2.006667  0.294444  0.093333  2.655556  12.288889  35.611111   
..         ...       ...       ...       ...       ...        ...        ...   
71   19.777778  2.026667  0.426667  0.102222  1.033333  15.833333  43.822222   
106  20.277778  2.046667  0.505556  0.176667  6.355556  21.422222  16.055556   
270  31.922222  1.824444  0.158889  0.033333  0.877778   4.522222  29.155556   
435  30.777778  2.017778  0.301111  0.103333  1.077778   9.855556  49.455556   
102  19.122222  2.005556  0.427778  0.191667  1.983333  19.783333  23.105556   

          PM10      PM2.5         RH   

In [93]:
#Using a 85% training data set split and 15% validation set split approach
np.random.seed(44)

data=originaldata
# Shuffle the DataFrame randomly
data = data.sample(frac=1, random_state=42)

# Calculate the split point
split_point = int(0.85 * len(data))

# Split the DataFrame into training and validation sets
train = data[:split_point]
validation = data[split_point:]


print(len(train))
print(len(validation))


488
87


In [94]:
data=train
# Separate features (X) and labels (y) from data
X = data.iloc[:, :-1].values

X = np.array(X)

y = data.iloc[:, -1].values
y = np.array(y)


# Normalize the features to have zero mean and unit variance
X = (X - np.mean(X, axis=0)) / np.std(X)


# Define initial bias, weight, learning rate, iteration, and regularization parameter
b = 0.0
w = np.zeros(X.shape[1])
lr = 0.01
iteration = 1000
reg_param = 0.1

# Initialize Adagrad learning rate parameters
lr_b = 0.0
lr_w = np.zeros(X.shape[1])

# Perform gradient descent with Adagrad
for i in range(iteration):
    b_grad = 0.0
    w_grad = np.zeros(X.shape[1],dtype=float)
    w_grad=w_grad.astype(float)
    for j in range(X.shape[0]):
        y_pred = np.dot(w, X[j]) + b
        b_grad += -2.0*(y[j] - y_pred) * 1
        w_grad = w_grad + -2.0*(y[j] - y_pred) * X[j]
        
    # Add regularization to the weight gradient
    w_grad += 2*reg_param * w
    # Update Adagrad learning rate parameters
    lr_b += b_grad ** 2
    lr_w = lr_w+ w_grad ** 2
    # Update bias and weight using Adagrad learning rate
    b -= lr / np.sqrt(lr_b) * b_grad
    w = w- lr / ((lr_w)**0.5) * w_grad

# Print the final bias and weight values
print('Final bias:', b)
print('Final weights:', w)

Final bias: 0.08954918032786954
Final weights: [-0.011222987608892883 0.1556404988261343 0.19293320376984716
 0.06244566419167483 -0.02867272816241873 -0.4866919838627843
 0.520474888414615 0.3296736072484568 -0.3293526226105651
 -0.2068593097374685 0.5454735241655596 -0.5668642592286438
 0.1621331642679746 -0.2554377283762627 0.24825792009028375
 -0.4589836762953669 -0.46494517698994864 -0.34188110180421555
 0.18237548693038652]


In [95]:
#TRAINING RMSE: Above uses 85% data to train the model
deviation=0
for j in range(X.shape[0]):
        y_pred = np.dot(w, X[j]) + b        
        deviation+= (y[j]-y_pred)**2

RMSE= np.sqrt(deviation/X.shape[0])
print(RMSE)

0.4810199281296279


In [96]:
#TEST RMSE: Above uses 25% data to validate the model
deviation=0
data=validation
# Separate features (X) and labels (y) from data
X = data.iloc[:, :-1].values

# Normalize the features to have zero mean and unit variance
X = (X - np.mean(X, axis=0)) / np.std(X)
print(X)
X = np.array(X)

y = data.iloc[:, -1].values
y = np.array(y)
for j in range(X.shape[0]):
        y_pred = np.dot(w, X[j]) + b        
        deviation+= (y[j]-y_pred)**2

RMSE= np.sqrt(deviation/X.shape[0])
print(RMSE)

[[2.187768990159995 0.034549380473165914 0.0013730880201780562 ...
  -0.00967787479383812 0.052943667989820344 0.016007236536050115]
 [3.3516757558071744 -0.10701800272434561 0.00047883341300233065 ...
  0.004492621289100351 -0.02134825322170174 0.044210651070053834]
 [-0.33815633103175585 0.04087795153933259 -0.00047045224692268196 ...
  -0.011191228744443199 -0.03373024009028876 -0.052093691241178484]
 ...
 [-0.3133923572945818 0.05711211210036888 -0.0008556696161676027 ...
  -0.009127564266345365 -0.05849421382746278 -0.059935616257950255]
 [-2.7402617835376364 -0.13769781463206676 2.482722782079631e-05 ...
  0.007932062085930076 0.12723558920134243 0.0014240075574920611]
 [0.8257504346154234 0.06412857132590156 -0.001378464617285723 ...
  -0.008439676106979419 0.04056168112123333 -0.08896449658319314]]
0.3964848156915088


In [ ]:
#Predicting test result data


#Processing test data



# Read CSV file
final = pd.read_csv(r"C:\Users\Phoebe Tan\OneDrive - National University of Singapore\Desktop\Taiwan\Data Mining\test_X.csv", header=None)

# Create a list of new headers
new_headers = ["Index","ItemName", "Hour 1", "Hour 2", "Hour 3", "Hour 4", "Hour 5", "Hour 6", "Hour 7", "Hour 8", "Hour 9"]

# Insert the new headers as the first row of the dataframe
final.columns = new_headers + [str(i) for i in range(1, len(final.columns) - len(new_headers) + 1)]
final.columns = [col.strip() for col in final.columns]
# Display the modified dataframe
print(final)

   
print(final.loc[final['Index']=='index_0'])

In [ ]:
final[['Hour 1', 'Hour 2', 'Hour 3', 'Hour 4', 'Hour 5','Hour 6', 'Hour 7', 'Hour 8', 'Hour 9']]= df[['Hour 1', 'Hour 2', 'Hour 3', 'Hour 4', 'Hour 5',
'Hour 6', 'Hour 7', 'Hour 8', 'Hour 9']].apply(pd.to_numeric)

# calculate the mean and median of the Hour 1 to 9 columns
final["Mean"] = final.iloc[:, 2:].mean(axis=1)

print(final)



In [ ]:
# Replace index_i with i
final['Index'] = final['Index'].replace({'index_': ''}, regex=True)

# convert the column Index from character to integer
final['Index'] = final['Index'].astype(int)
print(final)

In [ ]:
    
# Find the row indices with at least one NaN value
nan_rows =final.isna().any(axis=1)
nan_rows[(nan_rows==True)]
# Print the number of rows with NA values
print(sum(nan_rows==True))

In [ ]:
# Create a list of column names
columns = ['AMB_TEMP', 'CH4', 'CO', 'NMHC' ,'NO' ,'NO2', 'NOx', 'O3', 'PM10', 'PM2.5','RAINFALL' ,'RH' ,'SO2' ,'THC' ,'WD_HR', 'WIND_DIREC' ,'WIND_SPEED' ,'WS_HR']

# Create an empty DataFrame with the specified columns
newfinal = pd.DataFrame(columns=columns)


# insert Id column at beginning
newfinal.insert(0, 'id', range(0, 244))
# remove trailing white spaces from the 'ItemName' column
final['ItemName'] = final['ItemName'].str.strip()

# iterate through each id
for i in range(244):
    id_df = final.loc[final['Index'] == i] # select rows with the iterated id value
    for index, row in id_df.iterrows():
        item_name = row['ItemName']
        mean =row['Mean']
        newfinal.loc[newfinal['id'] == i,item_name] = mean # add the value in the Mean column to the new dataset column='ItemName' where 'ItemName'= item name of the value in 'ItemName' column of the iterated row
   

# print the new dataset
print(newfinal)

#rows_with_missing_values = newfinal[newfinal.isnull().any(axis=1)]
#print(rows_with_missing_values)



In [244]:

data=newfinal
X = data.iloc[:, 1:].values

X = np.array(X)

print(X)
# Normalize the features to have zero mean and unit variance
X = (X - np.mean(X, axis=0)) / np.std(X)

print(len(w))

#Initialize y predicted values
predicted= np.zeros(X.shape[0])


for j in range(X.shape[0]):
    y_pred = np.dot(w, X[j]) + b
    predicted[j]=y_pred
 


# Print the final bias and weight values
print('Final bias:', b)
print('Final weights:', w)

[[11.68888888888889 15.666666666666666 14.433333333333334 ...
  12.700000000000001 10.944444444444445 7.800000000000001]
 [8.38888888888889 8.433333333333332 10.855555555555556 ...
  14.422222222222224 15.122222222222222 17.933333333333334]
 [16.822222222222223 20.533333333333335 15.655555555555557 ...
  19.52222222222222 17.61111111111111 17.8]
 ...
 [18.18888888888889 8.200000000000001 26.12222222222222 ...
  14.066666666666665 23.477777777777778 37.488888888888894]
 [15.966666666666669 55.81111111111111 23.77777777777778 ...
  28.23333333333333 25.966666666666665 20.61111111111111]
 [46.422222222222224 11.577777777777778 40.06666666666667 ... 17.4
  24.499999999999996 15.733333333333333]]
Final bias: 0.08579710144927584
Final weights: [0.02927152491912405 0.24050138070143776 0.06833702080947508
 -0.04357360092235361 -0.3435287458814501 0.34994645142892566
 0.29133473785742764 -0.1757468009669007 -0.13956353922592732
 0.48939950430110163 -0.5543193428232913 0.20158938402819754
 -0.10

In [246]:
print(predicted)

[ 0.15126731 -0.16224372 -0.03762188 -0.38551171 -0.04159506 -0.32595385
 -0.32817192 -0.47476811 -0.06390199 -0.31852369 -0.56057006 -0.69420277
 -0.59121075 -0.52225642 -0.61802956 -0.68485182 -0.58392081 -0.58749047
 -0.31463089 -0.67170747 -0.55764982 -0.49868641 -0.35126721 -0.54053044
 -0.5351446  -0.43272292 -0.1801937   0.11656822 -0.5444248  -0.12812706
 -0.15097087 -0.01109523  0.39641818  0.36525831  0.36867113  0.39587376
  0.39458552  0.3903258   0.38535393  0.38318775  0.39498315  0.39212596
  0.38326527  0.39891918  0.38959238  0.40881653  0.40033837  0.39964196
  0.38906175  0.40717817  0.3891257   0.40405519  0.39114692  0.39656262
  0.39793456  0.3976802   0.39291319  0.38423962  0.39081944  0.40077357
  0.386634    0.39491151  0.39402078  0.39135817  0.44572363  0.3938606
  0.41175006  0.44781527  0.4548117   0.43515218  0.42211574  0.42009538
  0.45238196  0.44210875  0.43706492  0.44425842  0.45556631  0.45488922
  0.45702257  0.45201258  0.45045951  0.45701462  0.